# The best neighborhood

### this project is comparing neighborhoods based one the unique venues that exist in it

this project will only work on neywork dataset because i couldnt get any other neighborhoods dataset else where 



In [1]:
import requests # library to handle requests
import pandas as pd # library for data analsysis
import numpy as np # library to handle data in a vectorized manner
import random # library for random number generation

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # module to convert an addre|ss into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 

import json 
    
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize

!conda install -c conda-forge folium=0.5.0 --yes
import folium # plotting library

print('Folium installed')
print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2019.6.16  |       hecc5488_0         145 KB  conda-forge
    certifi-2019.6.16          |           py36_1         149 KB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    openssl-1.1.1c             |       h516909a_0         2.1 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.49-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

### Define credentials of foursquare API

In [2]:
CLIENT_ID = 'VYYCVYU2HWX3GT32SS5L5MKEZJIYFJX2NQA4FM1GVPO5ABHP' # your Foursquare ID
CLIENT_SECRET = 'WX5CTWB3X1HXAFCWRGGOH40C3ZVAVXHL1420ARZ325XE0TX0' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: VYYCVYU2HWX3GT32SS5L5MKEZJIYFJX2NQA4FM1GVPO5ABHP
CLIENT_SECRET:WX5CTWB3X1HXAFCWRGGOH40C3ZVAVXHL1420ARZ325XE0TX0


### download and import newyork neighborhood dataset

In [3]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset

In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

### Transform it into a Dataframe

In [95]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [96]:
neighborhoods_data = newyork_data['features']

In [97]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [98]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [9]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


## Map the neighborhoods

In [10]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

# this Project targets NY as a Whole so it wont specify Manhatten


In [11]:
neighborhoods.loc[0, 'Neighborhood']

'Wakefield'

## get the venues in Wakefield

In [12]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = neighborhoods.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Wakefield are 40.89470517661, -73.84720052054902.


In [13]:
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)


In [14]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5d42cdaf018cbb002c694ddc'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Wakefield',
  'headerFullLocation': 'Wakefield, Bronx',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 8,
  'suggestedBounds': {'ne': {'lat': 40.899205181110005,
    'lng': -73.84125857127495},
   'sw': {'lat': 40.89020517211, 'lng': -73.8531424698231}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4c537892fd2ea593cb077a28',
       'name': 'Lollipops Gelato',
       'location': {'address': '4120 Baychester Ave',
        'crossStreet': 'Edenwald & Bussing Ave',
        'lat': 40.894123150205274,
        'lng': -73.84589162362325,
        'labeledLatLn

In [15]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [16]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name            categories        lat  \
0                         Lollipops Gelato          Dessert Shop  40.894123   
1                                 Rite Aid              Pharmacy  40.896649   
2                         Carvel Ice Cream        Ice Cream Shop  40.890487   
3  Cooler Runnings Jamaican Restaurant Inc  Caribbean Restaurant  40.898276   
4                                  Dunkin'            Donut Shop  40.890459   

         lng  
0 -73.845892  
1 -73.844846  
2 -73.848568  
3 -73.850381  
4 -73.849089

In [17]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

8 venues were returned by Foursquare.


In [18]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [19]:
newyork_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [20]:
print(newyork_venues.shape)
newyork_venues.head()

(10386, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

                                     Venue  Venue Latitude  Venue Longitude  \
0                         Lollipops Gelato       40.894123       -73.845892   
1                                 Rite Aid       40.896649       -73.844846   
2                         Carvel Ice Cream       40.890487       -73.848568   
3  Cooler Runnings Jamaican Restaurant Inc       40.898276       -73.850381   
4                                  Dunkin'       40.890459       -73.849089   

         Venue Category  
0          Dessert Shop  
1              Pharmacy  
2        Ice Cream Shop  
3  Caribbean Restaurant  
4            Donut Shop

In [21]:
newyork_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                               
Allerton                               29                      29     29   
Annadale                               13                      13     13   
Arden Heights                           4                       4      4   
Arlington                               5                       5      5   
Arrochar                               21                      21     21   
Arverne                                18                      18     18   
Astoria                               100                     100    100   
Astoria Heights                        15                      15     15   
Auburndale                             18                      18     18   
Bath Beach                             47                      47     47   
Battery Park City                      99                      99     99   
Bay Ridge                              85                      85     85   
Bay Terrace                            51                      51     51   
Baychester                             22                      22     22   
Bayside                                72                      72     72   
Bayswater                               3                       3      3   
Bedford Park                           39                      39     39   
Bedford Stuyvesant                     27                      27     27   
Beechhurst                             15                      15     15   
Bellaire                                9                       9      9   
Belle Harbor                           18                      18     18   
Bellerose                              18                      18     18   
Belmont                                99                      99     99   
Bensonhurst                            34                      34     34   
Bergen Beach                            6                       6      6   
Blissville                             20                      20     20   
Bloomfield                              5                       5      5   
Boerum Hill                            89                      89     89   
Borough Park                           25                      25     25   
Breezy Point                            6                       6      6   
...                                   ...                     ...    ...   
Travis                                 16                      16     16   
Tribeca                               100                     100    100   
Tudor City                             83                      83     83   
Turtle Bay                            100                     100    100   
Unionport                              23                      23     23   
University Heights                     19                      19     19   
Upper East Side                       100                     100    100   
Upper West Side                       100                     100    100   
Utopia                                 16                      16     16   
Van Nest                               19                      19     19   
Vinegar Hill                           28                      28     28   
Wakefield                               8                       8      8   
Washington Heights                     86                      86     86   
Weeksville                             16                      16     16   
West Brighton                          36                      36     36   
West Farms                             22                      22     22   
West Village                          100                     100    100   
Westchester Square                     30                      30     30   
Westerleigh                             4                       4      4   
Whitestone                              7                       7   

In [22]:
x=newyork_venues.groupby('Neighborhood').count()
newyork_venues

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Wakefield              40.894705              -73.847201   
1         Wakefield              40.894705              -73.847201   
2         Wakefield              40.894705              -73.847201   
3         Wakefield              40.894705              -73.847201   
4         Wakefield              40.894705              -73.847201   
5         Wakefield              40.894705              -73.847201   
6         Wakefield              40.894705              -73.847201   
7         Wakefield              40.894705              -73.847201   
8        Co-op City              40.874294              -73.829939   
9        Co-op City              40.874294              -73.829939   
10       Co-op City              40.874294              -73.829939   
11       Co-op City              40.874294              -73.829939   
12       Co-op City              40.874294              -73.829939   
13       Co-op City              40.874294              -73.829939   
14       Co-op City              40.874294              -73.829939   
15       Co-op City              40.874294              -73.829939   
16       Co-op City              40.874294              -73.829939   
17       Co-op City              40.874294              -73.829939   
18       Co-op City              40.874294              -73.829939   
19       Co-op City              40.874294              -73.829939   
20       Co-op City              40.874294              -73.829939   
21       Co-op City              40.874294              -73.829939   
22       Co-op City              40.874294              -73.829939   
23       Co-op City              40.874294              -73.829939   
24      Eastchester              40.887556              -73.827806   
25      Eastchester              40.887556              -73.827806   
26      Eastchester              40.887556              -73.827806   
27      Eastchester              40.887556              -73.827806   
28      Eastchester              40.887556              -73.827806   
29      Eastchester              40.887556              -73.827806   
...             ...                    ...                     ...   
10356       Hammels              40.587338              -73.805530   
10357       Hammels              40.587338              -73.805530   
10358       Hammels              40.587338              -73.805530   
10359       Hammels              40.587338              -73.805530   
10360       Hammels              40.587338              -73.805530   
10361     Bayswater              40.611322              -73.765968   
10362     Bayswater              40.611322              -73.765968   
10363     Bayswater              40.611322              -73.765968   
10364  Queensbridge              40.756091              -73.945631   
10365  Queensbridge              40.756091              -73.945631   
10366  Queensbridge              40.756091              -73.945631   
10367  Queensbridge              40.756091              -73.945631   
10368  Queensbridge              40.756091              -73.945631   
10369  Queensbridge              40.756091              -73.945631   
10370  Queensbridge              40.756091              -73.945631   
10371  Queensbridge              40.756091              -73.945631   
10372  Queensbridge              40.756091              -73.945631   
10373  Queensbridge              40.756091              -73.945631   
10374  Queensbridge              40.756091              -73.945631   
10375  Queensbridge              40.756091              -73.945631   
10376  Queensbridge              40.756091              -73.945631   
10377  Queensbridge              40.756091              -73.945631   
10378  Queensbridge              40.756091              -73.945631   
10379  Queensbridge              40.756091              -73.945631   
10380     Fox Hills              40.617311              -74.081740   
10381     Fox Hil

NameError: name 'newyork_venues2' is not defined

In [ ]:
newyork_venues.reset_index()


In [24]:
newyork_venues.groupby(['Neighborhood'])['Venue Category'].unique()

Neighborhood
Allerton              [Fast Food Restaurant, Martial Arts Dojo, Pizz...
Annadale              [Sports Bar, Diner, Restaurant, Train Station,...
Arden Heights         [Pizza Place, Coffee Shop, Pharmacy, Business ...
Arlington             [Deli / Bodega, Bus Stop, American Restaurant,...
Arrochar              [Pizza Place, Italian Restaurant, Outdoors & R...
Arverne               [Beach, Surf Spot, Board Shop, Pizza Place, Th...
Astoria               [Brazilian Restaurant, Gym, Gourmet Shop, Seaf...
Astoria Heights       [Plaza, Italian Restaurant, Burger Joint, Pizz...
Auburndale            [Italian Restaurant, Athletics & Sports, Misce...
Bath Beach            [Park, Surf Spot, German Restaurant, Ice Cream...
Battery Park City     [Park, Gym, Food Court, Plaza, Shopping Mall, ...
Bay Ridge             [Spa, Bagel Shop, Juice Bar, Breakfast Spot, T...
Bay Terrace           [Bakery, Supermarket, American Restaurant, Fur...
Baychester            [Spanish Restaurant, Gym / Fi

In [25]:
NY= newyork_venues.groupby(['Neighborhood'])['Venue Category'].unique()

In [26]:
NY.index

Index(['Allerton', 'Annadale', 'Arden Heights', 'Arlington', 'Arrochar',
       'Arverne', 'Astoria', 'Astoria Heights', 'Auburndale', 'Bath Beach',
       ...
       'Williamsbridge', 'Williamsburg', 'Willowbrook', 'Windsor Terrace',
       'Wingate', 'Woodhaven', 'Woodlawn', 'Woodrow', 'Woodside', 'Yorkville'],
      dtype='object', name='Neighborhood', length=301)

In [27]:
NY2 = pd.DataFrame(list(map(np.ravel, NY)))
NY2

0                              1   \
0               Fast Food Restaurant              Martial Arts Dojo   
1                         Sports Bar                          Diner   
2                        Pizza Place                    Coffee Shop   
3                      Deli / Bodega                       Bus Stop   
4                        Pizza Place             Italian Restaurant   
5                              Beach                      Surf Spot   
6               Brazilian Restaurant                            Gym   
7                              Plaza             Italian Restaurant   
8                 Italian Restaurant             Athletics & Sports   
9                               Park                      Surf Spot   
10                              Park                            Gym   
11                               Spa                     Bagel Shop   
12                            Bakery                    Supermarket   
13                Spanish Restaurant           Gym / Fitness Center   
14                  Greek Restaurant                         Bakery   
15        Construction & Landscaping                     Playground   
16                              Park                  Deli / Bodega   
17                          Boutique                            Bar   
18                     Deli / Bodega                    Pizza Place   
19                Italian Restaurant             Chinese Restaurant   
20                             Beach             Mexican Restaurant   
21                             Diner            American Restaurant   
22                Italian Restaurant                  Deli / Bodega   
23                Italian Restaurant                 Cosmetics Shop   
24                        Donut Shop                 Baseball Field   
25                               Bar            Sporting Goods Shop   
26                 Recreation Center                     Theme Park   
27                Italian Restaurant            Japanese Restaurant   
28                       Pizza Place            American Restaurant   
29               Monument / Landmark                          Trail   
..                               ...                            ...   
271                              Gym             Spanish Restaurant   
272                             Park                   Cycle Studio   
273                             Park                    Yoga Studio   
274                           Museum                           Café   
275                        Juice Bar      Latin American Restaurant   
276        Latin American Restaurant             African Restaurant   
277               Italian Restaurant  Vegetarian / Vegan Restaurant   
278  Southern / Soul Food Restaurant                  Movie Theater   
279        South American Restaurant            Indie Movie Theater   
280                      Pizza Place                    Coffee Shop   
281              American Restaurant                        Factory   
282                     Dessert Shop                       Pharmacy   
283                       Restaurant                           Café   
284                             Café                   Cocktail Bar   
285               Italian Restaurant                    Coffee Shop   
286                           Lounge                          Diner   
287               Italian Restaurant             Chinese Restaurant   
288               Mexican Restaurant      Latin American Restaurant   
289                           Arcade              Convenience Store   
290                     Dance Studio                  Deli / Bodega   
291                       Soup Place                      Nightclub   
292                              Bar              Korean Restaurant   
293                       Bagel Shop                  Deli / Bodega   
294              Arts & Crafts Store                   Antique Shop   
295                        BBQ Joint                      

In [28]:
NY2['Neighborhood'] = NY.index
NY2.set_index('Neighborhood', inplace=True, verify_integrity=False)

In [29]:
NY2

0   \
Neighborhood                                          
Allerton                       Fast Food Restaurant   
Annadale                                 Sports Bar   
Arden Heights                           Pizza Place   
Arlington                             Deli / Bodega   
Arrochar                                Pizza Place   
Arverne                                       Beach   
Astoria                        Brazilian Restaurant   
Astoria Heights                               Plaza   
Auburndale                       Italian Restaurant   
Bath Beach                                     Park   
Battery Park City                              Park   
Bay Ridge                                       Spa   
Bay Terrace                                  Bakery   
Baychester                       Spanish Restaurant   
Bayside                            Greek Restaurant   
Bayswater                Construction & Landscaping   
Bedford Park                                   Park   
Bedford Stuyvesant                         Boutique   
Beechhurst                            Deli / Bodega   
Bellaire                         Italian Restaurant   
Belle Harbor                                  Beach   
Bellerose                                     Diner   
Belmont                          Italian Restaurant   
Bensonhurst                      Italian Restaurant   
Bergen Beach                             Donut Shop   
Blissville                                      Bar   
Bloomfield                        Recreation Center   
Boerum Hill                      Italian Restaurant   
Borough Park                            Pizza Place   
Breezy Point                    Monument / Landmark   
...                                             ...   
Travis                                          Gym   
Tribeca                                        Park   
Tudor City                                     Park   
Turtle Bay                                   Museum   
Unionport                                 Juice Bar   
University Heights        Latin American Restaurant   
Upper East Side                  Italian Restaurant   
Upper West Side     Southern / Soul Food Restaurant   
Utopia                    South American Restaurant   
Van Nest                                Pizza Place   
Vinegar Hill                    American Restaurant   
Wakefield                              Dessert Shop   
Washington Heights                       Restaurant   
Weeksville                                     Café   
West Brighton                    Italian Restaurant   
West Farms                                   Lounge   
West Village                     Italian Restaurant   
Westchester Square               Mexican Restaurant   
Westerleigh                                  Arcade   
Whitestone                             Dance Studio   
Williamsbridge                           Soup Place   
Williamsburg                                    Bar   
Willowbrook                              Bagel Shop   
Windsor Terrace                 Arts & Crafts Store   
Wingate                                   BBQ Joint   
Woodhaven                                Nail Salon   
Woodlawn                                Pizza Place   
Woodrow                            Sushi Restaurant   
Woodside                            Thai Restaurant   
Yorkville                                 Wine Shop   

                                               1                           2   \
Neighborhood                                                                    
Allerton                        Martial Arts Dojo                 Pizza Place   
Annadale                                    Diner                  Restaurant   
Arden Heights                         Coffee Shop                    Pharmacy   
Arlington                                Bus Stop         American Restaurant   
Arrochar                       Italian Restaurant       Outdoors & Recreation   
Arverne         

## now we have each nieghborhood with every type of venues that exist in it and no duplicates 

## which means we have every services that every neighborhood contains

In [30]:
NY3 = NY2.reset_index()
NYcluster = NY3.drop('Neighborhood', 1)
NYcluster

0                              1   \
0               Fast Food Restaurant              Martial Arts Dojo   
1                         Sports Bar                          Diner   
2                        Pizza Place                    Coffee Shop   
3                      Deli / Bodega                       Bus Stop   
4                        Pizza Place             Italian Restaurant   
5                              Beach                      Surf Spot   
6               Brazilian Restaurant                            Gym   
7                              Plaza             Italian Restaurant   
8                 Italian Restaurant             Athletics & Sports   
9                               Park                      Surf Spot   
10                              Park                            Gym   
11                               Spa                     Bagel Shop   
12                            Bakery                    Supermarket   
13                Spanish Restaurant           Gym / Fitness Center   
14                  Greek Restaurant                         Bakery   
15        Construction & Landscaping                     Playground   
16                              Park                  Deli / Bodega   
17                          Boutique                            Bar   
18                     Deli / Bodega                    Pizza Place   
19                Italian Restaurant             Chinese Restaurant   
20                             Beach             Mexican Restaurant   
21                             Diner            American Restaurant   
22                Italian Restaurant                  Deli / Bodega   
23                Italian Restaurant                 Cosmetics Shop   
24                        Donut Shop                 Baseball Field   
25                               Bar            Sporting Goods Shop   
26                 Recreation Center                     Theme Park   
27                Italian Restaurant            Japanese Restaurant   
28                       Pizza Place            American Restaurant   
29               Monument / Landmark                          Trail   
..                               ...                            ...   
271                              Gym             Spanish Restaurant   
272                             Park                   Cycle Studio   
273                             Park                    Yoga Studio   
274                           Museum                           Café   
275                        Juice Bar      Latin American Restaurant   
276        Latin American Restaurant             African Restaurant   
277               Italian Restaurant  Vegetarian / Vegan Restaurant   
278  Southern / Soul Food Restaurant                  Movie Theater   
279        South American Restaurant            Indie Movie Theater   
280                      Pizza Place                    Coffee Shop   
281              American Restaurant                        Factory   
282                     Dessert Shop                       Pharmacy   
283                       Restaurant                           Café   
284                             Café                   Cocktail Bar   
285               Italian Restaurant                    Coffee Shop   
286                           Lounge                          Diner   
287               Italian Restaurant             Chinese Restaurant   
288               Mexican Restaurant      Latin American Restaurant   
289                           Arcade              Convenience Store   
290                     Dance Studio                  Deli / Bodega   
291                       Soup Place                      Nightclub   
292                              Bar              Korean Restaurant   
293                       Bagel Shop                  Deli / Bodega   
294              Arts & Crafts Store                   Antique Shop   
295                        BBQ Joint                      

In [31]:
# import k-means from clustering stage
from sklearn.cluster import KMeans

In [32]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors


In [33]:
# one hot encoding
ny_onehot = pd.get_dummies(newyork_venues[['Venue Category']], prefix="", prefix_sep="")

ny_onehot["Neighborhoods"]=newyork_venues["Neighborhood"]

# move neighborhood column to the first column
fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
ny_onehot = ny_onehot[fixed_columns]

ny_onehot.head(50)

Neighborhoods  Accessories Store  Adult Boutique  Afghan Restaurant  \
0      Wakefield                  0               0                  0   
1      Wakefield                  0               0                  0   
2      Wakefield                  0               0                  0   
3      Wakefield                  0               0                  0   
4      Wakefield                  0               0                  0   
5      Wakefield                  0               0                  0   
6      Wakefield                  0               0                  0   
7      Wakefield                  0               0                  0   
8     Co-op City                  0               0                  0   
9     Co-op City                  0               0                  0   
10    Co-op City                  0               0                  0   
11    Co-op City                  0               0                  0   
12    Co-op City                  0               0                  0   
13    Co-op City                  0               0                  0   
14    Co-op City                  0               0                  0   
15    Co-op City                  0               0                  0   
16    Co-op City                  0               0                  0   
17    Co-op City                  0               0                  0   
18    Co-op City                  0               0                  0   
19    Co-op City                  0               0                  0   
20    Co-op City                  0               0                  0   
21    Co-op City                  0               0                  0   
22    Co-op City                  0               0                  0   
23    Co-op City                  1               0                  0   
24   Eastchester                  0               0                  0   
25   Eastchester                  0               0                  0   
26   Eastchester                  0               0                  0   
27   Eastchester                  0               0                  0   
28   Eastchester                  0               0                  0   
29   Eastchester                  0               0                  0   
30   Eastchester                  0               0                  0   
31   Eastchester                  0               0                  0   
32   Eastchester                  0               0                  0   
33   Eastchester                  0               0                  0   
34   Eastchester                  0               0                  0   
35   Eastchester                  0               0                  0   
36   Eastchester                  0               0                  0   
37   Eastchester                  0               0                  0   
38   Eastchester                  0               0                  0   
39   Eastchester                  0               0                  0   
40   Eastchester                  0               0                  0   
41   Eastchester                  0               0                  0   
42   Eastchester                  0               0                  0   
43     Fieldston                  0               0                  0   
44     Fieldston                  0               0                  0   
45     Fieldston                  0               0                  0   
46     Fieldston                  0               0                  0   
47     Riverdale                  0               0                  0   
48     Riverdale                  0               0                  0   
49     Riverdale                  0               0                  0   

    African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                    0                 0                    0             0   
1                    0                 0                    0         

In [42]:
x = ny_onehot.groupby(["Neighborhoods"]).mean().reset_index()
x.head()

Neighborhoods  Accessories Store  Adult Boutique  Afghan Restaurant  \
0       Allerton                0.0             0.0                0.0   
1       Annadale                0.0             0.0                0.0   
2  Arden Heights                0.0             0.0                0.0   
3      Arlington                0.0             0.0                0.0   
4       Arrochar                0.0             0.0                0.0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                 0.0               0.0             0.000000           0.0   
1                 0.0               0.0             0.076923           0.0   
2                 0.0               0.0             0.000000           0.0   
3                 0.0               0.0             0.200000           0.0   
4                 0.0               0.0             0.000000           0.0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0     0.0               0.0                     0.0          0.0         0.0   
1     0.0               0.0                     0.0          0.0         0.0   
2     0.0               0.0                     0.0          0.0         0.0   
3     0.0               0.0                     0.0          0.0         0.0   
4     0.0               0.0                     0.0          0.0         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                  0.0                   0.0               0.0   
1                  0.0                   0.0               0.0   
2                  0.0                   0.0               0.0   
3                  0.0                   0.0               0.0   
4                  0.0                   0.0               0.0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0            0.000000         0.0                    0.0                  0.0   
1            0.000000         0.0                    0.0                  0.0   
2            0.000000         0.0                    0.0                  0.0   
3            0.000000         0.0                    0.0                  0.0   
4            0.047619         0.0                    0.0                  0.0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0.0              0.0        0.0         0.0    0.000000     0.0   
1            0.0              0.0        0.0         0.0    0.000000     0.0   
2            0.0              0.0        0.0         0.0    0.000000     0.0   
3            0.0              0.0        0.0         0.0    0.000000     0.0   
4            0.0              0.0        0.0         0.0    0.047619     0.0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  Bath House  \
0   0.0  0.0             0.0               0.0               0.0         0.0   
1   0.0  0.0             0.0               0.0               0.0         0.0   
2   0.0  0.0             0.0               0.0               0.0         0.0   
3   0.0  0.0             0.0               0.0               0.0         0.0   
4   0.0  0.0             0.0               0.0               0.0         0.0   

   Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0    0.0        0.0              0.0       0.0          0.0         0.0   
1    0.0        0.0              0.0       0.0          0.0         0.0   
2    0.0        0.0              0.0       0.0          0.0         0.0   
3    0.0        0.0              0.0       0.0          0.0         0.0   
4    0.0        0.0              0.0       0.0          0.0         0.0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0            0.0                       0.0        0.0         0.0     0.0   
1            0.0                       0.0        0.0         0.0     0.0   
2            0.0                       0.0        0.0         0.0     0.0   
3  

In [ ]:
ny_onehot = ny_onehot[ny_onehot.columns.difference(['Neighborhoods'])].apply(lambda x: [y if y <= 0.000001 else 1.0 for y in x])

In [47]:
x.drop(['Neighborhoods'],1, inplace = True)
x.head()

Accessories Store  Adult Boutique  Afghan Restaurant  African Restaurant  \
0                0.0             0.0                0.0                 0.0   
1                0.0             0.0                0.0                 0.0   
2                0.0             0.0                0.0                 0.0   
3                0.0             0.0                0.0                 0.0   
4                0.0             0.0                0.0                 0.0   

   Airport Terminal  American Restaurant  Antique Shop  Arcade  \
0               0.0             0.000000           0.0     0.0   
1               0.0             0.076923           0.0     0.0   
2               0.0             0.000000           0.0     0.0   
3               0.0             0.200000           0.0     0.0   
4               0.0             0.000000           0.0     0.0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0               0.0                     0.0          0.0         0.0   
1               0.0                     0.0          0.0         0.0   
2               0.0                     0.0          0.0         0.0   
3               0.0                     0.0          0.0         0.0   
4               0.0                     0.0          0.0         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                  0.0                   0.0               0.0   
1                  0.0                   0.0               0.0   
2                  0.0                   0.0               0.0   
3                  0.0                   0.0               0.0   
4                  0.0                   0.0               0.0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0            0.000000         0.0                    0.0                  0.0   
1            0.000000         0.0                    0.0                  0.0   
2            0.000000         0.0                    0.0                  0.0   
3            0.000000         0.0                    0.0                  0.0   
4            0.047619         0.0                    0.0                  0.0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0.0              0.0        0.0         0.0    0.000000     0.0   
1            0.0              0.0        0.0         0.0    0.000000     0.0   
2            0.0              0.0        0.0         0.0    0.000000     0.0   
3            0.0              0.0        0.0         0.0    0.000000     0.0   
4            0.0              0.0        0.0         0.0    0.047619     0.0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  Bath House  \
0   0.0  0.0             0.0               0.0               0.0         0.0   
1   0.0  0.0             0.0               0.0               0.0         0.0   
2   0.0  0.0             0.0               0.0               0.0         0.0   
3   0.0  0.0             0.0               0.0               0.0         0.0   
4   0.0  0.0             0.0               0.0               0.0         0.0   

   Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0    0.0        0.0              0.0       0.0          0.0         0.0   
1    0.0        0.0              0.0       0.0          0.0         0.0   
2    0.0        0.0              0.0       0.0          0.0         0.0   
3    0.0        0.0              0.0       0.0          0.0         0.0   
4    0.0        0.0              0.0       0.0          0.0         0.0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0            0.0                       0.0        0.0         0.0     0.0   
1            0.0                       0.0        0.0         0.0     0.0   
2            0.0                       0.0        0.0         0.0     0.0   
3            0.0                       0.0        0.0         0.0     0.0   
4            0.0

In [50]:

x = np.where(a > 0, 1, a).tolist()
print(x)

[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 1.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0

In [61]:
y = pd.DataFrame(x)
y.head()
z= ny_onehot.columns.difference(['Neighborhoods'])
z = z.tolist()

In [52]:
z= ny_onehot.columns.difference(['Neighborhoods'])
z

Index(['Accessories Store', 'Adult Boutique', 'Afghan Restaurant',
       'African Restaurant', 'Airport Terminal', 'American Restaurant',
       'Antique Shop', 'Arcade', 'Arepa Restaurant', 'Argentinian Restaurant',
       ...
       'Waste Facility', 'Watch Shop', 'Waterfront', 'Weight Loss Center',
       'Whisky Bar', 'Wine Bar', 'Wine Shop', 'Wings Joint', 'Women's Store',
       'Yoga Studio'],
      dtype='object', length=429)

In [66]:
y.columns = [z]
y.head()

Accessories Store Adult Boutique Afghan Restaurant African Restaurant  \
0               0.0            0.0               0.0                0.0   
1               0.0            0.0               0.0                0.0   
2               0.0            0.0               0.0                0.0   
3               0.0            0.0               0.0                0.0   
4               0.0            0.0               0.0                0.0   

  Airport Terminal American Restaurant Antique Shop Arcade Arepa Restaurant  \
0              0.0                 0.0          0.0    0.0              0.0   
1              0.0                 1.0          0.0    0.0              0.0   
2              0.0                 0.0          0.0    0.0              0.0   
3              0.0                 1.0          0.0    0.0              0.0   
4              0.0                 0.0          0.0    0.0              0.0   

  Argentinian Restaurant Art Gallery Art Museum Arts & Crafts Store  \
0                    0.0         0.0        0.0                 0.0   
1                    0.0         0.0        0.0                 0.0   
2                    0.0         0.0        0.0                 0.0   
3                    0.0         0.0        0.0                 0.0   
4                    0.0         0.0        0.0                 0.0   

  Arts & Entertainment Asian Restaurant Athletics & Sports Auditorium  \
0                  0.0              0.0                0.0        0.0   
1                  0.0              0.0                0.0        0.0   
2                  0.0              0.0                0.0        0.0   
3                  0.0              0.0                0.0        0.0   
4                  0.0              0.0                1.0        0.0   

  Australian Restaurant Austrian Restaurant Auto Workshop Automotive Shop  \
0                   0.0                 0.0           0.0             0.0   
1                   0.0                 0.0           0.0             0.0   
2                   0.0                 0.0           0.0             0.0   
3                   0.0                 0.0           0.0             0.0   
4                   0.0                 0.0           0.0             0.0   

  BBQ Joint Baby Store Bagel Shop Bakery Bank  Bar Baseball Field  \
0       0.0        0.0        0.0    0.0  0.0  0.0            0.0   
1       0.0        0.0        0.0    0.0  0.0  0.0            0.0   
2       0.0        0.0        0.0    0.0  0.0  0.0            0.0   
3       0.0        0.0        0.0    0.0  0.0  0.0            0.0   
4       0.0        0.0        1.0    0.0  0.0  0.0            0.0   

  Baseball Stadium Basketball Court Bath House Beach Beach Bar  \
0              0.0              0.0        0.0   0.0       0.0   
1              0.0              0.0        0.0   0.0       0.0   
2              0.0              0.0        0.0   0.0       0.0   
3              0.0              0.0        0.0   0.0       0.0   
4              0.0              0.0        0.0   0.0       0.0   

  Bed & Breakfast Beer Bar Beer Garden Beer Store Big Box Store  \
0             0.0      0.0         0.0        0.0           0.0   
1             0.0      0.0         0.0        0.0           0.0   
2             0.0      0.0         0.0        0.0           0.0   
3             0.0      0.0         0.0        0.0           0.0   
4             0.0      0.0         0.0        0.0           0.0   

  Bike Rental / Bike Share Bike Shop Bike Trail Bistro Board Shop  \
0                      0.0       0.0        0.0    0.0        0.0   
1                      0.0       0.0        0.0    0.0        0.0   
2                      0.0       0.0        0.0    0.0        0.0   
3                      0.0       0.0        0.0    0.0        0.0   
4                      0.0       0.0        0.0    0.0        0.0   

  Boat or Ferry Bookstore Boutique Bowling Alley Boxing Gym  \
0           0.0       0.0      0.0           0.0      

 # Now i have converted all values of store or service occurence into 1 or 0 either it exist in the neighborhood or not
 
## now we will cluster the similar neighborhoods

In [67]:
# set number of clusters
kclusters = 5

ycluster = y

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ycluster)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 


array([3, 0, 0, 0, 0, 0, 1, 3, 3, 2], dtype=int32)

In [73]:
q = ny_onehot.groupby(["Neighborhoods"]).mean().reset_index()
q.head()

Neighborhoods  Accessories Store  Adult Boutique  Afghan Restaurant  \
0       Allerton                0.0             0.0                0.0   
1       Annadale                0.0             0.0                0.0   
2  Arden Heights                0.0             0.0                0.0   
3      Arlington                0.0             0.0                0.0   
4       Arrochar                0.0             0.0                0.0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                 0.0               0.0             0.000000           0.0   
1                 0.0               0.0             0.076923           0.0   
2                 0.0               0.0             0.000000           0.0   
3                 0.0               0.0             0.200000           0.0   
4                 0.0               0.0             0.000000           0.0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0     0.0               0.0                     0.0          0.0         0.0   
1     0.0               0.0                     0.0          0.0         0.0   
2     0.0               0.0                     0.0          0.0         0.0   
3     0.0               0.0                     0.0          0.0         0.0   
4     0.0               0.0                     0.0          0.0         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                  0.0                   0.0               0.0   
1                  0.0                   0.0               0.0   
2                  0.0                   0.0               0.0   
3                  0.0                   0.0               0.0   
4                  0.0                   0.0               0.0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0            0.000000         0.0                    0.0                  0.0   
1            0.000000         0.0                    0.0                  0.0   
2            0.000000         0.0                    0.0                  0.0   
3            0.000000         0.0                    0.0                  0.0   
4            0.047619         0.0                    0.0                  0.0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0.0              0.0        0.0         0.0    0.000000     0.0   
1            0.0              0.0        0.0         0.0    0.000000     0.0   
2            0.0              0.0        0.0         0.0    0.000000     0.0   
3            0.0              0.0        0.0         0.0    0.000000     0.0   
4            0.0              0.0        0.0         0.0    0.047619     0.0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  Bath House  \
0   0.0  0.0             0.0               0.0               0.0         0.0   
1   0.0  0.0             0.0               0.0               0.0         0.0   
2   0.0  0.0             0.0               0.0               0.0         0.0   
3   0.0  0.0             0.0               0.0               0.0         0.0   
4   0.0  0.0             0.0               0.0               0.0         0.0   

   Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0    0.0        0.0              0.0       0.0          0.0         0.0   
1    0.0        0.0              0.0       0.0          0.0         0.0   
2    0.0        0.0              0.0       0.0          0.0         0.0   
3    0.0        0.0              0.0       0.0          0.0         0.0   
4    0.0        0.0              0.0       0.0          0.0         0.0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0            0.0                       0.0        0.0         0.0     0.0   
1            0.0                       0.0        0.0         0.0     0.0   
2            0.0                       0.0        0.0         0.0     0.0   
3  

In [77]:
y['Neighborhoods'] = q["Neighborhoods"]

In [78]:
y.head()

Accessories Store Adult Boutique Afghan Restaurant African Restaurant  \
0               0.0            0.0               0.0                0.0   
1               0.0            0.0               0.0                0.0   
2               0.0            0.0               0.0                0.0   
3               0.0            0.0               0.0                0.0   
4               0.0            0.0               0.0                0.0   

  Airport Terminal American Restaurant Antique Shop Arcade Arepa Restaurant  \
0              0.0                 0.0          0.0    0.0              0.0   
1              0.0                 1.0          0.0    0.0              0.0   
2              0.0                 0.0          0.0    0.0              0.0   
3              0.0                 1.0          0.0    0.0              0.0   
4              0.0                 0.0          0.0    0.0              0.0   

  Argentinian Restaurant Art Gallery Art Museum Arts & Crafts Store  \
0                    0.0         0.0        0.0                 0.0   
1                    0.0         0.0        0.0                 0.0   
2                    0.0         0.0        0.0                 0.0   
3                    0.0         0.0        0.0                 0.0   
4                    0.0         0.0        0.0                 0.0   

  Arts & Entertainment Asian Restaurant Athletics & Sports Auditorium  \
0                  0.0              0.0                0.0        0.0   
1                  0.0              0.0                0.0        0.0   
2                  0.0              0.0                0.0        0.0   
3                  0.0              0.0                0.0        0.0   
4                  0.0              0.0                1.0        0.0   

  Australian Restaurant Austrian Restaurant Auto Workshop Automotive Shop  \
0                   0.0                 0.0           0.0             0.0   
1                   0.0                 0.0           0.0             0.0   
2                   0.0                 0.0           0.0             0.0   
3                   0.0                 0.0           0.0             0.0   
4                   0.0                 0.0           0.0             0.0   

  BBQ Joint Baby Store Bagel Shop Bakery Bank  Bar Baseball Field  \
0       0.0        0.0        0.0    0.0  0.0  0.0            0.0   
1       0.0        0.0        0.0    0.0  0.0  0.0            0.0   
2       0.0        0.0        0.0    0.0  0.0  0.0            0.0   
3       0.0        0.0        0.0    0.0  0.0  0.0            0.0   
4       0.0        0.0        1.0    0.0  0.0  0.0            0.0   

  Baseball Stadium Basketball Court Bath House Beach Beach Bar  \
0              0.0              0.0        0.0   0.0       0.0   
1              0.0              0.0        0.0   0.0       0.0   
2              0.0              0.0        0.0   0.0       0.0   
3              0.0              0.0        0.0   0.0       0.0   
4              0.0              0.0        0.0   0.0       0.0   

  Bed & Breakfast Beer Bar Beer Garden Beer Store Big Box Store  \
0             0.0      0.0         0.0        0.0           0.0   
1             0.0      0.0         0.0        0.0           0.0   
2             0.0      0.0         0.0        0.0           0.0   
3             0.0      0.0         0.0        0.0           0.0   
4             0.0      0.0         0.0        0.0           0.0   

  Bike Rental / Bike Share Bike Shop Bike Trail Bistro Board Shop  \
0                      0.0       0.0        0.0    0.0        0.0   
1                      0.0       0.0        0.0    0.0        0.0   
2                      0.0       0.0        0.0    0.0        0.0   
3                      0.0       0.0        0.0    0.0        0.0   
4                      0.0       0.0        0.0    0.0        0.0   

  Boat or Ferry Bookstore Boutique Bowling Alley Boxing Gym  \
0           0.0       0.0      0.0           0.0      

# After making the Clustering label lists we need to add it to the Dataframe in order to plot it

In [79]:
fixed_columns = [y.columns[-1]] + list(y.columns[:-1])
y = y[fixed_columns]
y.head()

Neighborhoods Accessories Store Adult Boutique Afghan Restaurant  \
0       Allerton               0.0            0.0               0.0   
1       Annadale               0.0            0.0               0.0   
2  Arden Heights               0.0            0.0               0.0   
3      Arlington               0.0            0.0               0.0   
4       Arrochar               0.0            0.0               0.0   

  African Restaurant Airport Terminal American Restaurant Antique Shop Arcade  \
0                0.0              0.0                 0.0          0.0    0.0   
1                0.0              0.0                 1.0          0.0    0.0   
2                0.0              0.0                 0.0          0.0    0.0   
3                0.0              0.0                 1.0          0.0    0.0   
4                0.0              0.0                 0.0          0.0    0.0   

  Arepa Restaurant Argentinian Restaurant Art Gallery Art Museum  \
0              0.0                    0.0         0.0        0.0   
1              0.0                    0.0         0.0        0.0   
2              0.0                    0.0         0.0        0.0   
3              0.0                    0.0         0.0        0.0   
4              0.0                    0.0         0.0        0.0   

  Arts & Crafts Store Arts & Entertainment Asian Restaurant  \
0                 0.0                  0.0              0.0   
1                 0.0                  0.0              0.0   
2                 0.0                  0.0              0.0   
3                 0.0                  0.0              0.0   
4                 0.0                  0.0              0.0   

  Athletics & Sports Auditorium Australian Restaurant Austrian Restaurant  \
0                0.0        0.0                   0.0                 0.0   
1                0.0        0.0                   0.0                 0.0   
2                0.0        0.0                   0.0                 0.0   
3                0.0        0.0                   0.0                 0.0   
4                1.0        0.0                   0.0                 0.0   

  Auto Workshop Automotive Shop BBQ Joint Baby Store Bagel Shop Bakery Bank  \
0           0.0             0.0       0.0        0.0        0.0    0.0  0.0   
1           0.0             0.0       0.0        0.0        0.0    0.0  0.0   
2           0.0             0.0       0.0        0.0        0.0    0.0  0.0   
3           0.0             0.0       0.0        0.0        0.0    0.0  0.0   
4           0.0             0.0       0.0        0.0        1.0    0.0  0.0   

   Bar Baseball Field Baseball Stadium Basketball Court Bath House Beach  \
0  0.0            0.0              0.0              0.0        0.0   0.0   
1  0.0            0.0              0.0              0.0        0.0   0.0   
2  0.0            0.0              0.0              0.0        0.0   0.0   
3  0.0            0.0              0.0              0.0        0.0   0.0   
4  0.0            0.0              0.0              0.0        0.0   0.0   

  Beach Bar Bed & Breakfast Beer Bar Beer Garden Beer Store Big Box Store  \
0       0.0             0.0      0.0         0.0        0.0           0.0   
1       0.0             0.0      0.0         0.0        0.0           0.0   
2       0.0             0.0      0.0         0.0        0.0           0.0   
3       0.0             0.0      0.0         0.0        0.0           0.0   
4       0.0             0.0      0.0         0.0        0.0           0.0   

  Bike Rental / Bike Share Bike Shop Bike Trail Bistro Board Shop  \
0                      0.0       0.0        0.0    0.0        0.0   
1                      0.0       0.0        0.0    0.0        0.0   
2                      0.0       0.0        0.0    0.0        0.0   
3                      0.0       0.0        0.0    0.0        0.0   
4                      0.0       0.0        0.0    0.0        0.0   

  Boat or Ferry Bookstore Bo

In [80]:
y.insert(0, 'Cluster Labels', kmeans.labels_)
y.head()

Cluster Labels  Neighborhoods Accessories Store Adult Boutique  \
0              3       Allerton               0.0            0.0   
1              0       Annadale               0.0            0.0   
2              0  Arden Heights               0.0            0.0   
3              0      Arlington               0.0            0.0   
4              0       Arrochar               0.0            0.0   

  Afghan Restaurant African Restaurant Airport Terminal American Restaurant  \
0               0.0                0.0              0.0                 0.0   
1               0.0                0.0              0.0                 1.0   
2               0.0                0.0              0.0                 0.0   
3               0.0                0.0              0.0                 1.0   
4               0.0                0.0              0.0                 0.0   

  Antique Shop Arcade Arepa Restaurant Argentinian Restaurant Art Gallery  \
0          0.0    0.0              0.0                    0.0         0.0   
1          0.0    0.0              0.0                    0.0         0.0   
2          0.0    0.0              0.0                    0.0         0.0   
3          0.0    0.0              0.0                    0.0         0.0   
4          0.0    0.0              0.0                    0.0         0.0   

  Art Museum Arts & Crafts Store Arts & Entertainment Asian Restaurant  \
0        0.0                 0.0                  0.0              0.0   
1        0.0                 0.0                  0.0              0.0   
2        0.0                 0.0                  0.0              0.0   
3        0.0                 0.0                  0.0              0.0   
4        0.0                 0.0                  0.0              0.0   

  Athletics & Sports Auditorium Australian Restaurant Austrian Restaurant  \
0                0.0        0.0                   0.0                 0.0   
1                0.0        0.0                   0.0                 0.0   
2                0.0        0.0                   0.0                 0.0   
3                0.0        0.0                   0.0                 0.0   
4                1.0        0.0                   0.0                 0.0   

  Auto Workshop Automotive Shop BBQ Joint Baby Store Bagel Shop Bakery Bank  \
0           0.0             0.0       0.0        0.0        0.0    0.0  0.0   
1           0.0             0.0       0.0        0.0        0.0    0.0  0.0   
2           0.0             0.0       0.0        0.0        0.0    0.0  0.0   
3           0.0             0.0       0.0        0.0        0.0    0.0  0.0   
4           0.0             0.0       0.0        0.0        1.0    0.0  0.0   

   Bar Baseball Field Baseball Stadium Basketball Court Bath House Beach  \
0  0.0            0.0              0.0              0.0        0.0   0.0   
1  0.0            0.0              0.0              0.0        0.0   0.0   
2  0.0            0.0              0.0              0.0        0.0   0.0   
3  0.0            0.0              0.0              0.0        0.0   0.0   
4  0.0            0.0              0.0              0.0        0.0   0.0   

  Beach Bar Bed & Breakfast Beer Bar Beer Garden Beer Store Big Box Store  \
0       0.0             0.0      0.0         0.0        0.0           0.0   
1       0.0             0.0      0.0         0.0        0.0           0.0   
2       0.0             0.0      0.0         0.0        0.0           0.0   
3       0.0             0.0      0.0         0.0        0.0           0.0   
4       0.0             0.0      0.0         0.0        0.0           0.0   

  Bike Rental / Bike Share Bike Shop Bike Trail Bistro Board Shop  \
0                      0.0       0.0        0.0    0.0        0.0   
1                      0.0       0.0        0.0    0.0        0.0   
2                      0.0       0.0        0.0    0.0        0.0   
3                      0.0       0.0        0.0    0.0        0.0   
4      

In [218]:

y

Cluster Labels              Neighborhoods Accessories Store  \
0                3                   Allerton               0.0   
1                0                   Annadale               0.0   
2                0              Arden Heights               0.0   
3                0                  Arlington               0.0   
4                0                   Arrochar               0.0   
5                0                    Arverne               0.0   
6                1                    Astoria               0.0   
7                3            Astoria Heights               0.0   
8                3                 Auburndale               0.0   
9                2                 Bath Beach               0.0   
10               4          Battery Park City               0.0   
11               2                  Bay Ridge               0.0   
12               2                Bay Terrace               1.0   
13               3                 Baychester               0.0   
14               1                    Bayside               0.0   
15               0                  Bayswater               0.0   
16               3               Bedford Park               0.0   
17               0         Bedford Stuyvesant               0.0   
18               3                 Beechhurst               0.0   
19               0                   Bellaire               0.0   
20               3               Belle Harbor               0.0   
21               3                  Bellerose               0.0   
22               2                    Belmont               0.0   
23               2                Bensonhurst               0.0   
24               0               Bergen Beach               0.0   
25               0                 Blissville               0.0   
26               0                 Bloomfield               0.0   
27               1                Boerum Hill               0.0   
28               3               Borough Park               0.0   
29               0               Breezy Point               0.0   
30               0                  Briarwood               0.0   
31               2             Brighton Beach               0.0   
32               0              Broad Channel               0.0   
33               3          Broadway Junction               0.0   
34               3                  Bronxdale               0.0   
35               1           Brooklyn Heights               0.0   
36               0                 Brookville               0.0   
37               3                Brownsville               0.0   
38               2                 Bulls Head               0.0   
39               2                   Bushwick               0.0   
40               0               Butler Manor               0.0   
41               0            Cambria Heights               0.0   
42               0                   Canarsie               0.0   
43               4              Carnegie Hill               0.0   
44               1            Carroll Gardens               0.0   
45               3                Castle Hill               0.0   
46               3          Castleton Corners               0.0   
47               3             Central Harlem               0.0   
48               2                 Charleston               0.0   
49               4                    Chelsea               0.0   
50               4                  Chinatown               0.0   
51               3                City Island               0.0   
52               2                  City Line               0.0   
53               4               Civic Center               0.0   
54               3          Claremont Village               0.0   
55               0               Clason Point               0.0   
56               3                    Clifton               0.0   
57               4                    Clinton               0.0   
58               1               Clinton Hill      

In [214]:
y.sum(axis=1)

0      25.0
1      10.0
2       4.0
3       5.0
4      17.0
5      13.0
6      60.0
7      18.0
8      21.0
9      39.0
10     62.0
11     53.0
12     37.0
13     23.0
14     50.0
15      3.0
16     26.0
17     21.0
18     18.0
19      7.0
20     17.0
21     18.0
22     50.0
23     30.0
24      5.0
25     16.0
26      5.0
27     64.0
28     19.0
29      5.0
30      8.0
31     32.0
32      5.0
33     17.0
34     17.0
35     68.0
36      1.0
37     21.0
38     35.0
39     44.0
40      4.0
41     10.0
42      5.0
43     63.0
44     63.0
45     11.0
46     15.0
47     37.0
48     32.0
49     69.0
50     65.0
51     27.0
52     35.0
53     63.0
54     16.0
55      7.0
56     18.0
57     63.0
58     55.0
59     19.0
60     69.0
61     32.0
62      8.0
63     24.0
64     31.0
65     17.0
66     19.0
67      5.0
68     18.0
69     20.0
70     41.0
71     19.0
72     22.0
73     74.0
74     55.0
75      6.0
76     11.0
77     18.0
78     34.0
79     11.0
80     20.0
81     63.0
82     42.0
83  

In [196]:
q = n.sort_values(by=['Neighborhood'])
q = q.rename({'Neighborhood': 'Neighborhoods'},axis=1)
q.head()

Borough  Neighborhoods   Latitude  Longitude
298          Bronx       Allerton  40.865788 -73.859319
215  Staten Island       Annadale  40.538114 -74.178549
241  Staten Island  Arden Heights  40.549286 -74.185887
227  Staten Island      Arlington  40.635325 -74.165104
228  Staten Island       Arrochar  40.596313 -74.067124

In [162]:
q.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 302 entries, 298 to 108
Data columns (total 4 columns):
Borough          302 non-null object
Neighborhoods    302 non-null object
Latitude         302 non-null float64
Longitude        302 non-null float64
dtypes: float64(2), object(2)
memory usage: 11.8+ KB


In [202]:
q.insert(0, 'Cluster Labels', kmeans.labels_)

In [203]:
q.head()

Cluster Labels        Borough  Neighborhoods   Latitude  Longitude
298               3          Bronx       Allerton  40.865788 -73.859319
215               0  Staten Island       Annadale  40.538114 -74.178549
241               0  Staten Island  Arden Heights  40.549286 -74.185887
227               0  Staten Island      Arlington  40.635325 -74.165104
228               0  Staten Island       Arrochar  40.596313 -74.067124

In [205]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(q['Latitude'], q['Longitude'], q['Neighborhoods'], q['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

SyntaxError: invalid syntax (<ipython-input-167-5ddf9dc859a6>, line 2)

[['Allerton'],
 ['Annadale'],
 ['Arden Heights'],
 ['Arlington'],
 ['Arrochar'],
 ['Arverne'],
 ['Astoria'],
 ['Astoria Heights'],
 ['Auburndale'],
 ['Bath Beach'],
 ['Battery Park City'],
 ['Bay Ridge'],
 ['Bay Terrace'],
 ['Baychester'],
 ['Bayside'],
 ['Bayswater'],
 ['Bedford Park'],
 ['Bedford Stuyvesant'],
 ['Beechhurst'],
 ['Bellaire'],
 ['Belle Harbor'],
 ['Bellerose'],
 ['Belmont'],
 ['Bensonhurst'],
 ['Bergen Beach'],
 ['Blissville'],
 ['Bloomfield'],
 ['Boerum Hill'],
 ['Borough Park'],
 ['Breezy Point'],
 ['Briarwood'],
 ['Brighton Beach'],
 ['Broad Channel'],
 ['Broadway Junction'],
 ['Bronxdale'],
 ['Brooklyn Heights'],
 ['Brookville'],
 ['Brownsville'],
 ['Bulls Head'],
 ['Bushwick'],
 ['Butler Manor'],
 ['Cambria Heights'],
 ['Canarsie'],
 ['Carnegie Hill'],
 ['Carroll Gardens'],
 ['Castle Hill'],
 ['Castleton Corners'],
 ['Central Harlem'],
 ['Charleston'],
 ['Chelsea'],
 ['Chinatown'],
 ['City Island'],
 ['City Line'],
 ['Civic Center'],
 ['Claremont Village'],
 ['Cla

<class 'pandas.core.frame.DataFrame'>
Int64Index: 301 entries, 298 to 108
Data columns (total 4 columns):
Borough          301 non-null object
Neighborhoods    301 non-null object
Latitude         301 non-null float64
Longitude        301 non-null float64
dtypes: float64(2), object(2)
memory usage: 11.8+ KB
